# 3-7. 言語・知識 - 表現学習（エンベディング）
ある情報を数値のベクトルで表現することを埋め込みやembedding（エンべディング）と呼ぶ．
特に，自然言語を機械学習で扱おうとするとき，文字列をどう表現するかというのは大きな問題の一つになる．

代表的には，One-hotベクトルによる表現や，Word2Vecを用いた表現などが存在する．実用上ではこれらの処理をどのようにして行っていくのか，ゲームパッケージのタイトルを利用して具体的にみてみよう．

## データの取得・整形
[メディア芸術データベース・ラボ](https://mediag.bunka.go.jp/madb_lab/)上で提供されている[SPARQLクエリサービス](https://mediag.bunka.go.jp/madb_lab/lod/sparql/)を利用して，ゲームパッケージのデータを取得していく．

以下のコードを[SPARQLクエリサービス](https://mediag.bunka.go.jp/madb_lab/lod/sparql/)上に入力して実行する，または入力を省略した[こちらのURL](https://mediag.bunka.go.jp/madb_lab/lod/sparql/#query=PREFIX%20ma%3A%20%3Chttps%3A%2F%2Fmediaarts-db.bunka.go.jp%2Fdata%2Fproperty%23%3E%0APREFIX%20rdfs%3A%20%20%20%3Chttp%3A%2F%2Fwww.w3.org%2F2000%2F01%2Frdf-schema%23%3E%0APREFIX%20schema%3A%20%3Chttps%3A%2F%2Fschema.org%2F%3E%20SELECT%20%3F%E3%83%A9%E3%83%99%E3%83%AB%20%3F%E7%99%BA%E8%A1%8C%E8%80%85%20%3F%E3%83%97%E3%83%A9%E3%83%83%E3%83%88%E3%83%95%E3%82%A9%E3%83%BC%E3%83%A0%20%3F%E3%83%AC%E3%83%BC%E3%83%86%E3%82%A3%E3%83%B3%E3%82%B0%20%3F%E5%85%AC%E9%96%8B%E5%B9%B4%E6%9C%88%E6%97%A5%0AWHERE%20%7B%0A%20%20%3F%E3%82%A2%E3%82%A4%E3%83%86%E3%83%A0%0A%20%20%20%20%20%20%20%20schema%3Agenre%20%22%E3%82%B2%E3%83%BC%E3%83%A0%E3%83%91%E3%83%83%E3%82%B1%E3%83%BC%E3%82%B8%22%3B%0A%20%20%20%20%20%20%20%20schema%3AcontentRating%20%3F%E3%83%AC%E3%83%BC%E3%83%86%E3%82%A3%E3%83%B3%E3%82%B0%3B%0A%20%20%20%20%20%20%20%20schema%3AgamePlatform%20%3F%E3%83%97%E3%83%A9%E3%83%83%E3%83%88%E3%83%95%E3%82%A9%E3%83%BC%E3%83%A0%3B%0A%20%20%20%20%20%20%20%20schema%3Apublisher%20%3F%E7%99%BA%E8%A1%8C%E8%80%85%3B%0A%20%20%20%20%20%20%20%20rdfs%3Alabel%20%3F%E3%83%A9%E3%83%99%E3%83%AB%3B%0A%20%20%20%20%20%20%20%20ma%3AdatePublished%20%3F%E5%85%AC%E9%96%8B%E5%B9%B4%E6%9C%88%E6%97%A5.%0A%7D&endpoint=https%3A%2F%2Fmediag.bunka.go.jp%2Fsparql&requestMethod=POST&tabTitle=Query&headers=%7B%7D&contentTypeConstruct=application%2Fn-triples%2C*%2F*%3Bq%3D0.9&contentTypeSelect=application%2Fsparql-results%2Bjson%2C*%2F*%3Bq%3D0.9&outputFormat=table)から実行してデータを取得できる．
取得したCSVファイルを「ゲームパッケージ.csv」として保存し，このノートブック上にアップロードしよう．

※「3-4. ディープニューラルネットワーク（DNN）」，「3-4. 学習用データと学習済みモデル」，「3-6. 決定木」，「3-6. サポートベクターマシン」，「3-7. 形態素解析」，「3-7. かな漢字変換」と同じデータセットを作成するため，もし同じものを持っている場合は以下の取得作業は不要なので，そちらをアップロードしよう．

```
PREFIX ma: <https://mediaarts-db.bunka.go.jp/data/property#>
PREFIX rdfs:   <http://www.w3.org/2000/01/rdf-schema#>
PREFIX schema: <https://schema.org/> SELECT ?ラベル ?発行者 ?プラットフォーム ?レーティング ?公開年月日
WHERE {
  ?アイテム
        schema:genre "ゲームパッケージ";
        schema:contentRating ?レーティング;
        schema:gamePlatform ?プラットフォーム;
        schema:publisher ?発行者;
        rdfs:label ?ラベル;
        ma:datePublished ?公開年月日.
}
```

取得したデータセットを，Python上で扱いやすい形にしていく．
pandasというライブラリを用いて，csv形式のファイルの中身をDataFrameという型に変換し，扱っていく．

In [1]:
# 必要なモジュールのインポート
!pip install pykakasi
!pip install --upgrade gensim

from gensim.models import Word2Vec
import pykakasi
import pandas as pd
import numpy as np
import collections
from sklearn.preprocessing import OneHotEncoder

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.4/2.4 MB 11.0 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for jaconv: filename=jaconv-0.3.4-py3-none-any.whl size=16415 sha256=165a2eff172cfb166e1e787bcde455a4f04f190d6eedeb01397eb34d3f07bb70
  Stored in directory: /root/.cache/pip/wheels/46/8f/2e/a730bf1fca05b33e532d5d91dabdf406c9b718ec85b01b1b54
Successfully built jaconv


In [2]:
games = pd.read_csv("/content/ゲームパッケージ.csv")
games = games.drop_duplicates(subset='ラベル')
games = games.reset_index(drop=True)
games

ラベル  \
0                           Dance Dance Revolution GB2   
1                                     プロ野球 ファミスタ リターンズ   
2                                      プロ野球 ファミスタ 2011   
3                                              フロッガー3D   
4                                           ブレイブリーセカンド   
...                                                ...   
19452                 バイオショック インフィニット PlayStation Now版   
19453  バイオハザード リベレーションズ アンベールド エディション PlayStation Now版   
19454                           巫剣神威控 PlayStation Now版   
19455                 ネバーエンディング ナイトメア PlayStation Now版   
19456                   雷電IV OverKill PlayStation Now版   

                           発行者       プラットフォーム            レーティング       公開年月日  
0                      コナミ株式会社         ゲームボーイ  CERO D (17才以上対象)  2000-11-16  
1        株式会社バンダイナムコエンターテインメント      ニンテンドー3DS    CERO A (全年齢対象)  2015-10-08  
2              株式会社バンダイナムコゲームス      ニンテンドー3DS    CERO A (全年齢対象)  2011-03-31  
3         株式会社コナミデジタルエンタテインメント      ニンテンドー3DS    CERO A (全年齢対象)  2011-09-22  
4              株式会社スクウェア・エニックス      ニンテンドー3DS  CERO C (15才以上対象)  2015-04-23  
...                        ...            ...               ...         ...  
19452  テイクツー・インタラクティブ・ジャパン合同会社  プレイステーション Now  CERO D (17才以上対象)  2017-09-19  
19453                 株式会社カプコン  プレイステーション Now  CERO D (17才以上対象)  2016-09-20  
19454           アクティブゲーミングメディア  プレイステーション Now  CERO C (15才以上対象)  2017-07-20  
19455           アクティブゲーミングメディア  プレイステーション Now  CERO D (17才以上対象)  2017-07-20  
19456                       モス  プレイステーション Now    CERO A (全年齢対象)  2017-02-21  

[19457 rows x 5 columns]

## One-Hotベクトル
未知の単語が出てきた順にインデックスを振り，対応するインデックスの要素だけ1，あとは0というようなベクトルを作成する．
pykakasiというモジュールを用いて日本語の文章を単語に分割し，ワンホットベクトルにしていく．

In [3]:
# pykakasiのインスタンスを用意
kks = pykakasi.kakasi()

# ゲームタイトルに出てくる単語を順番に全て格納するリスト
words = []

for title in games['ラベル']:
  words.extend([token["orig"] for token in kks.convert(title)])

# ワンホットベクトルへのエンコードを行うインスタンスの作成
onehot_encoder = OneHotEncoder(sparse = False,dtype = int)

# ワンホットベクトルへの学習・変換を同時に行う
words_embedded = onehot_encoder.fit_transform(np.array(words).reshape(-1,1))

/usr/local/lib/python3.10/dist-packages/sklearn/preprocessing/_encoders.py:868: FutureWarning: `sparse` was renamed to `sparse_output` in version 1.2 and will be removed in 1.4. `sparse_output` is ignored unless you leave `sparse` to its default value.
  warnings.warn(


「パッケージ」という単語のベクトルを見てみよう．

In [4]:
# 出力が省略されないように閾値を変えておく
np.set_printoptions(threshold=100000)

input = "パッケージ"
print("onehotベクトルの次元数: ", len(words_embedded[0]))
print("元の単語: ", input)
print("ワンホットベクトル: ", onehot_encoder.transform([[input]]))

# 閾値を元に戻す
np.set_printoptions(threshold=1000)

onehotベクトルの次元数:  20323
元の単語:  パッケージ
ワンホットベクトル:  [[0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
  0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
  0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
  0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
  0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
  0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
  0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
  0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
  0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
  0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
  0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
  0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0
  0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 0 

One-Hotベクトル表現は，語彙数とベクトルの次元数が同じになってしまうという点で，計算効率の悪さや入力としての扱いづらさ（入力次元数が定まらないと機械学習がしづらい）などの問題がある．


## Word2Vec
One-Hotベクトルの欠点を克服するのがこのWord2Vecである．これは単語同士の意味の近さをベクトルの大きさや方向の近さで表現する手法であり，指定した次元に埋め込むこともできるため，効率的に学習が行える．
Word2Vecモデルの学習を実際にやってみよう．

In [5]:
# ゲームタイトルを単語を分割したリストを順番に全て格納するリスト
words = []

for title in games['ラベル']:
  words.append([token["orig"] for token in kks.convert(title)])

In [6]:
# Word2Vecモデルを学習
model = Word2Vec(words,  sg=1, vector_size=100, window=3, min_count=0) # 引数sg=1でskip-gram（周りの単語を推測する手法）で学習することを指定

In [7]:
# "パッケージ"のベクトル表現を出力
input = "パッケージ"
result = model.wv.get_vector(input)
print("onehotベクトルの次元数: ", len(result))
print("元の単語: ", input)
print("ベクトル: ", result)


onehotベクトルの次元数:  100
元の単語:  パッケージ
ベクトル:  [-0.11668929  0.09766782  0.3968426   0.6236199  -0.34263754 -0.26765057
  0.36841166  0.39545757 -0.7935258  -0.13745552 -0.153762   -0.2411714
 -0.45867485  0.35353434 -0.05605572 -0.17603661  0.2606729   0.25922826
 -0.4332906  -0.8751171   0.38124487 -0.2746471   0.9497776  -0.31293562
 -0.26312435 -0.18485972 -0.50300866  0.42192176 -0.6822334   0.31044954
  0.24615403 -0.22320043 -0.18758088 -0.69846314 -0.28777418  0.10628433
  0.00291802  0.05891388  0.08581531 -0.21064182  0.34355447 -0.56263196
 -0.5777083   0.06062189  0.33344656  0.0877355  -0.38855493  0.18607187
  0.5731279   0.18241204 -0.02902607 -0.06122071  0.21697947 -0.24158446
 -0.3627133  -0.11245427 -0.04041747 -0.4449694  -0.37351665  0.17147596
  0.3219174  -0.23757496  0.18068212  0.031368    0.207157    0.35256016
 -0.06172541  0.6798512  -0.6101884  -0.11404646 -0.04860069  0.46427938
  0.2708793  -0.11087355  0.4998917   0.11074626  0.27610767  0.33965242
  0.0981058

Word2Vecの特徴として，ベクトルの近さと単語の近さに関係があるという点がある．
実際に「パッケージ」に近いベクトルを出力してみよう．

In [8]:
# "パッケージ"に近しい意味を持つ単語を出力
for i in model.wv.most_similar('パッケージ'):
    print(i)

('ベスト', 0.9795853495597839)
('同梱', 0.9794086217880249)
(' PlayStation Now', 0.9755346775054932)
('替え', 0.9713441729545593)
('\u3000', 0.9557426571846008)
('吹き', 0.9538519978523254)
('ダウンロード', 0.9515132308006287)
(' of LOVE!', 0.951181948184967)
('プラチナコレクション', 0.9496081471443176)
('デラックス', 0.9489535689353943)


「パッケージ」に近い意味の単語を出力させてみると，「パッケージ版」のようにゲームタイトルの最後に「~~版」という形で載っていそうな単語が多く出力されていることがわかる．

この手法の欠点としては，きちんと単語同士の距離をベクトルに反映させるためには十分な量の学習データが必要であるという点である．今回の「ゲームタイトル」のようにあまり文章的ではない学習データでは，直感的にはわかりづらい結果が出てくることもある．
そのため，利用するデータの大きさや種類によって使い分けられると良い．